# El juego del Sudoku como un problema de optimización: una implementación en Gurobi Python

##### Pablo Yapura (ypf@agro.unlp.edu.ar)
##### Facultad de Ciencias Agrarias y Forestales
##### Universidad Nacional de La Plata

## Introducción

El Sudoku es un juego lógico extremadamente popular, en el que se colocan números naturales en una cuadrícula respetando ciertas reglas. Si bien existen variantes del siglo XIX que pueden ser consideradas como precursoras, la mayoría de los autores coinciden en que la versión moderna del juego data de 1979, año en el que se publicó con un nombre diferente en una revista de juegos y crucigramas en Estados Unidos de América (Bartlett et al., 2008). Aunque la revista no publicó la autoría del juego, muchos autores le acreditan este diseño contemporáneo a Howard Garns, un arquitecto que luego de su jubilación se dedicó a crear juegos. El juego se popularizó primero en Japón, país en el que fue introducido por una compañía comercial de juegos a mediados de la década de 1980. En poco tiempo, el juego tomó el nombre actual con el que es conocido en todo el mundo, Sudoku, y que refiere a que *los números deben permanecer solteros* (Bartlett et al., 2008). Actualmente es ofrecido como pasatiempo por una gran cantidad de diarios, revistas y sitios *web* de todo el mundo.

De una manera general, el juego del Sudoku se configura con una cuadrícula de dimensión $N \times N$ que se divide en subcuadrículas de dimensión $m \times n$ llamadas regiones, cuadros o bloques, cada uno de los cuales está compuesto por $m$ filas y $n$ columnas, siendo $N = m n$ puesto que el número de celdas en una región es igual al número de filas y de columnas de la cuadrícula. Aunque las celdas pueden estar completamente vacías, en el inicio del juego es común que un subconjunto contenga valores *dados* en el intervalo entero  $\left[\!\left[ 1, N \right]\!\right]$. Luego, las celdas vacías se deben completar con valores del mismo intervalo $\left[\!\left[ 1, N \right]\!\right]$, de forma tal que cada número entero del intervalo aparezca:

* solamente una vez en cada fila de la cuadrícula;
* solamente una vez en cada columna de la cuadrícula; y
* solamente una vez en cada región de la cuadrícula.

Matemáticamente hablando, estas reglas del juego se pueden considerar como condiciones que implican que cada celda de la cuadrícula solucionada debe contener un único número de la sucesión entera $\{1, 2, \ldots N \}$ y que cada fila, cada columna y cada región de la cuadrícula debe contener una permutación de esa sucesión.

---
## Formulación matemática del problema y su solución

Bartlett et al. (2008) expresaron que la solución de los juegos del Sudoku se puede encontrar de dos maneras diferentes. La primera consiste en programar una computadora para que emule la lógica que usaría un ser humano para resolverlo, en un abordaje que, en estos días, seguramente sería considerado como un legítimo problema del amplio campo de la inteligencia artificial. El segundo abordaje consiste en formular el problema de forma tal que se le pueda aplicar algún algoritmo matemático para encontrar la solución exacta, en caso de que exista. Con este segundo enfoque, Bartlett et al. (2008) presentaron una rigurosa formulación del juego del Sudoku como un problema de programación entera binaria, la cual seguiremos en general en este trabajo. Sin embargo, la formulación como un problema de optimización se habria originado en el ambiente educativo, tal como lo sugieren Weiss & Rasmussen (2007). Actualmente, el Sudoku como un problema de optimización es un ejemplo elemental de los intentos por ludificar el proceso de enseñanza-aprendizaje de la Investigación Operativa.

Para presentar su formulación, en este trabajo se usará una forma del problema en la que las regiones son rectangulares, es decir con $m \neq n$, y se adoptará la notación simbólica de Assencio (2017). En la Figura que se presenta a continuación se detalla la nomenclatura de los índices que se usarán para representar aspectos importantes del problema. Cada celda será indizada con el par de índices $(i,j)$ en la que $i$ y $j$ designan a la fila y a la columna de la celda, respectivamente. Para representar la ubicación de las regiones se usará otro par de índices $(I,J)$ en la que $I$ y $J$ designan a la fila y a la columna de la región, respectivamente. En la figura se presenta un juego de Sudoku con regiones de dimensión $m \times n = 2 \times 3$. Los índices de las celdas se muestran en el interior de las mismas y los índices de las regiones se muestran a la izquierda y arriba. La altura (número de filas) y el ancho (número de columnas) de la cuadrícula son iguales a $N = mn = 6$. Este juego tiene $n$ regiones en dirección vertical  y $m$ regiones en dirección horizontal. Además, las regiones se muestran con dos fondos en tonos de grises contrastantes.

<div align="center">
	<img width = "45%" src="https://drive.google.com/uc?id=1-wyXb7Ywr05mQrk1J7OCui1Vd54Vk12J">
</div>

Entonces, la formulación matemática del problema empieza definiendo las variables binarias de decisión de acuerdo con:

$$x_{ijk} = \left\{ \begin{array} {ll}
1, \ \text{si la celda $(i,j)$ contiene el entero $k$;} \\
0, \ \text{de otro modo.}
\end{array} \right.$$

Para $i = 1, 2, \ldots, N; j = 1, 2, \ldots, N; k = 1, 2, \ldots, N$. En total, se definen $N^3$ variables binarias de decisión.

Luego, cada una de las tres reglas del juego debe formularse como un conjunto particular de restricciones. La exigencia de que una permutación de $k = \{1, 2, \ldots N \}$ debe completar cada fila de la cuadrícula se puede escribir como:

$$\sum_{j=1}^N x_{ijk} = 1,$$

para $i = 1, 2, \ldots, N; k = 1, 2, \ldots, N$. Esto implica que se necesitan $N^2$ ecuaciones de este tipo.

La exigencia de que cada elemento de $k = \{1, 2, \ldots N \}$ debe aparecer una sola vez en cada columna de la cuadrícula se puede escribir como:

$$\sum_{i=1}^N x_{ijk} = 1,$$

para $j = 1, 2, \ldots, N; k = 1, 2, \ldots, N$. En consecuencia, también se necesitan $N^2$ ecuaciones de este tipo.

La tercera condición, es decir la exigencia de que una permutación de $k = \{1, 2, \ldots N \}$ debe completar cada región de la cuadrícula, es un poco más elaborada, pero se puede escribir como:

$$\sum_{i = Im - m + 1}^{Im} \sum_{j = Jn - n + 1}^{Jn} x_{ijk} = 1$$

para $I = 1, 2, \ldots, n$, $J = 1, 2, \ldots, m$, and $k = 1, 2, \ldots, N$. En este caso, también se necesitan $nmN = N^2$ ecuaciones de este tipo.

Más allá de las reglas del juego, también es necesario formular restricciones para que cada celda de la cuadrícula tome un único valor entre los $k = 1, 2, \ldots, N$ enteros posibles:

$$\sum_{k=1}^N x_{ijk} = 1,$$

para $i = 1, 2, \ldots, N; j = 1, 2, \ldots, N$. Una vez más, se necesitan $N^2$ ecuaciones de este tipo.

Si se define un conjunto auxiliar $\mathcal{C}$ conteniendo los tripletes que identifican a las celdas $(i,j)$ de la cuadrícula que recibieron a $k$ como el valor *dado* al inicio del juego, entonces se puede escribir:

$$x_{ijk} = 1,$$

para todo $(i,j,k)\in \mathcal{C}$. El número mínimo de *dados* que se deben suministrar para obtener una respuesta única es una pregunta más bien abierta desde el punto de vista teórico y, por ende, fuera del alcance de este trabajo. Sin embargo, para resolver un juego particular, debe recordarse que es un dato suministrado, de forma tal que resulta sencillo inferir la cantidad de restricciones de este tipo que se necesitan.

Por último, como en todo problema de programación matemática, es necesario hacer alguna consideración con respecto a la función objetivo. En rigor, como señalan Bartlett et al. (2008), el juego del Sudoku es un ejemplo sencillo de los conocidos como *problemas de satisfacción de restricciones*. En este tipo de problemas, lo que se intenta encontrar es una solución factible, es decir una que meramente satisfaga el conjunto de restricciones aplicables. Si bien se pueden emplear algoritmos específicos más eficientes, aquí interesa resolver el juego del Sudoku formulado como un problema de programación entera binaria y usando alguno de los algoritmos de optimización. En consecuencia, teóricamente no sería necesario especificar una función objetivo. Algunos programas (*e.g.* GLPK, Gurobi) son capaces de encontrar una solución óptima sin que se haya especificado una función objetivo, *i.e.* pueden funcionar como un algoritmo de solución para el problema de satisfacción de restricciones. Pero si el programa que se usará no puede optimizar sin que se le haya especificado una función objetivo, esta formulación puede resolver el requerimiento:

$$\text{min} \ z = \sum_{i=1}^N \sum_{j=1}^N \sum_{k=1}^N 0 x_{i, j, k},$$

para $i = 1, 2, \ldots, N; j = 1, 2, \ldots, N; k = 1, 2, \ldots, N$. En otras palabras, una función objetivo con todos sus coeficientes iguales a cero. Otra observación que se puede hacer con relación a este abordaje para resolver el juego del Sudoku es que no será capaz de encontrar soluciones alternativas para los mismos *dados*, las que pueden existir, claro está.

---
## Una implementación en Gurobi Python

A continuación se presenta la implementación del problema formulado, incluyendo la instalación del paquete gurobipy de Gurobi que incluye una licencia limitada para pruebas y que permite ejecutar el código en línea. La *traducción* del modelo algebraico a un programa informático codificado en Python que pueda ser solucionado por el *solver* de Gurobi es, en términos generales, autoexplicativa, dada la naturalidad de sus semejanzas.


In [1]:
# Primero se instala el paquete gurobipy y se importan los módulos necesarios
%pip install gurobipy
import numpy as np
import gurobipy as gp
from gurobipy import GRB

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.4/13.4 MB 991.6 kB/s eta 0:00:00


In [2]:
# A continuación se configura el juego
m = 2 # El número de filas de las regiones
n = 3 # El número de columnas de las regiones
N = m * n # La dimensión de la cuadrícula
sucesion = range(1, N+1) # Índices i, j, k
idx_fils_reg = range(1, n+1) # Índices I
idx_cols_reg = range(1, m+1) # Índices J
dados = np.array([
    [ 0 , 0 , 0 , 2 , 0 , 0 ],
    [ 0 , 0 , 0 , 4 , 5 , 0 ],
    [ 0 , 3 , 4 , 0 , 0 , 0 ],
    [ 0 , 0 , 0 , 1 , 4 , 0 ],
    [ 0 , 6 , 1 , 0 , 0 , 0 ],
    [ 0 , 0 , 5 , 0 , 0 , 0 ]
], dtype=int)

In [3]:
# La codificación del modelo propiamente dicho y su solución
with gp.Env() as amb, gp.Model("sudoku", env=amb) as modelo:
    # Definir las variables de decisión
    x = modelo.addVars(sucesion, sucesion, sucesion, vtype=GRB.BINARY, name="x")

    # Definir las restricciones
    modelo.addConstrs((x.sum(i, '*', k) == 1
                       for i in sucesion for k in sucesion), name="fil")
    modelo.addConstrs((x.sum('*', j, k) == 1
                       for j in sucesion for k in sucesion), name="col")
    modelo.addConstrs((x.sum([i for i in range(I*m-m+1, I*m+1)],
                             [j for j in range(J*n-n+1, J*n+1)], k) == 1
                       for I in idx_fils_reg for J in idx_cols_reg
                       for k in sucesion), name="reg")
    modelo.addConstrs((x.sum(i, j, '*') == 1
                       for i in sucesion for j in sucesion), name="cel")

    # Fijar los valores de las variables con los dados según recomienda Gurobi
    for i in range (N):
      for j in range (N):
        if dados[i][j] != 0:
          x[i+1, j+1, dados[i][j]].LB = 1

    # Grabar el archivo en formato (CPLEX) LP
    modelo.write("sudoku.lp")

    # Definir función objetivo: ¡no es necesario!

    # Optimizar
    modelo.optimize()

    # Recuperar un diccionario con la solución
    solucion = modelo.getAttr("X", x)

    # Imprimir la solución, con el fragmento de código de Gurobi
    print()
    print("******* Solución *******")
    print()
    for i in sucesion:
      linea_solucion = ''
      for j in sucesion:
        for k in sucesion:
          if solucion[i, j, k] > 0:
            linea_solucion += str(k) + ' '
      print(linea_solucion)
    print()
    print("************************")

Restricted license - for non-production use only - expires 2025-11-24
Gurobi Optimizer version 11.0.3 build v11.0.3rc0 (linux64 - "Ubuntu 22.04.3 LTS")

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Optimize a model with 144 rows, 216 columns and 864 nonzeros
Model fingerprint: 0x6d58757e
Variable types: 0 continuous, 216 integer (216 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [0e+00, 0e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Presolve removed 144 rows and 216 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.02 seconds (0.00 work units)
Thread count was 1 (of 2 available processors)

Solution count 1: 0 

Optimal solution found (tolerance 1.00e-04)
Best objective 0.000000000000e+00, best bound 0.000000000000e+00, gap 0.0000%

******* Solución **

---
## Bibliografía

Assencio, D. (2017). Solving Sudoku puzzles using linear programming. Linkedin personal blog. https://dassencio.org/99.

Bartlett, A. C., Chartier, T. P., Langville, A. N. & Rankin, T. D. (2008). An integer programming model for the Sudoku problem. Journal of Online Mathematics and its Applications 8 (1).

Weiss, H. J. & Rasmussen, R. A. (2007). Lessons from Modeling Sudoku in Excel. INFORMS Transactions on Education 7 (2). https://doi.org/10.1287/ited.7.2.178.

---
Este *notebook* se desarrolló con fines exclusivamente pedagógicos. Se agradecerá señalar los errores y compartir críticas y sugerencias. Por favor, envíelas por correo-e a ypf@agro.unlp.edu.ar.

[El juego del Sudoku como un problema de optimización: una implementación en Gurobi Python](https://colab.research.google.com/drive/1yRbkj8dMA2gK_bDEC7V675rnIZ1d-PQC?usp=sharing) © 2024 by Pablo Yapura is licensed under Creative Commons [Attribution-ShareAlike 4.0 International](https://creativecommons.org/licenses/by-sa/4.0/?ref=chooser-v1).